In [ ]:
#88
# 888
# 889
# 99, IF99

# Download data 

In [1]:
from datetime import datetime
from typing import List, Dict, Tuple

from vnpy.trader.engine import BaseEngine, MainEngine, EventEngine
from vnpy.trader.constant import Interval, Exchange
from vnpy.trader.object import BarData, HistoryRequest
from vnpy.trader.database import database_manager
from vnpy.trader.rqdata import rqdata_client

In [2]:
rqdata_client.init()

True

In [17]:
def download_data(symbol, exchange):
    start = datetime(2006,1,1)
    req = HistoryRequest(
        symbol=symbol,
        exchange=exchange,
        interval=Interval.DAILY,
        start=start,
        end=datetime.now()
    )

    data = rqdata_client.query_history(req)
    database_manager.save_bar_data(data)
    
    print("finish! symbol=",symbol, "count=", len(data))

In [ ]:
download_data("IC99", Exchange.CFFEX)

In [ ]:
database_manager.save_bar_data(data)

# GET ALL instuments

In [4]:
df=rqdata_client.get_all_futures()
df
# underlying_symbol
# exchange
# listed_date

order_book_id underlying_symbol  market_tplus    symbol  margin_rate  \
0            A0303                 A           0.0    豆一0303         0.05   
1            A0305                 A           0.0    豆一0305         0.05   
2            A0307                 A           0.0    豆一0307         0.05   
3            A0309                 A           0.0    豆一0309         0.05   
4            A0311                 A           0.0    豆一0311         0.05   
...            ...               ...           ...       ...          ...   
6609        PB2201                PB           0.0     铅2201         0.08   
6610        BC2201                BC           0.0   国际铜2201         0.08   
6611        BB2201                BB           0.0  细木工板2201         0.40   
6612        SR2201                SR           0.0   白砂糖2201         0.07   
6613        WR2201                WR           0.0    线材2201         0.07   

     maturity_date    type trading_code exchange    product  \
0       2003-03-14  Future        a0303      DCE  Commodity   
1       2003-05-23  Future        a0305      DCE  Commodity   
2       2003-07-14  Future        a0307      DCE  Commodity   
3       2003-09-12  Future        a0309      DCE  Commodity   
4       2003-11-14  Future        a0311      DCE  Commodity   
...            ...     ...          ...      ...        ...   
6609    2022-01-17  Future       pb2201     SHFE  Commodity   
6610    2022-01-17  Future       bc2201      INE  Commodity   
6611    2022-01-17  Future       bb2201      DCE  Commodity   
6612    2022-01-14  Future        SR201     CZCE  Commodity   
6613    2022-01-17  Future       wr2201     SHFE  Commodity   

      contract_multiplier  round_lot  \
0                    10.0        1.0   
1                    10.0        1.0   
2                    10.0        1.0   
3                    10.0        1.0   
4                    10.0        1.0   
...                   ...        ...   
6609                  5.0        1.0   
6610                  5.0        1.0   
6611                500.0        1.0   
6612                 10.0        1.0   
6613                 10.0        1.0   

                                        trading_hours listed_date  \
0     21:01-23:00,09:01-10:15,10:31-11:30,13:31-15:00  2002-03-15   
1     21:01-23:00,09:01-10:15,10:31-11:30,13:31-15:00  2002-03-15   
2     21:01-23:00,09:01-10:15,10:31-11:30,13:31-15:00  2002-03-15   
3     21:01-23:00,09:01-10:15,10:31-11:30,13:31-15:00  2002-05-22   
4     21:01-23:00,09:01-10:15,10:31-11:30,13:31-15:00  2002-05-22   
...                                               ...         ...   
6609  21:01-01:00,09:01-10:15,10:31-11:30,13:31-15:00  2021-01-18   
6610  21:01-01:00,09:01-10:15,10:31-11:30,13:31-15:00  2021-01-18   
6611              09:01-10:15,10:31-11:30,13:31-15:00  2021-01-18   
6612  21:01-23:00,09:01-10:15,10:31-11:30,13:31-15:00  2021-01-18   
6613              09:01-10:15,10:31-11:30,13:31-15:00  2021-01-18   

     industry_name de_listed_date underlying_order_book_id  
0               油脂     2003-03-14                     null  
1               油脂     2003-05-23                     null  
2               油脂     2003-07-14                     null  
3               油脂     2003-09-12                     null  
4               油脂     2003-11-14                     null  
...            ...            ...                      ...  
6609            有色     2022-01-17                     null  
6610            未知     2022-01-17                     null  
6611            建材     2022-01-17                     null  
6612           软商品     2022-01-14                     null  
6613          焦煤钢矿     2022-01-17                     null  

[6614 rows x 17 columns]

In [7]:
data_dict = df.transpose().to_dict()

In [8]:
data_dict[0]

{'order_book_id': 'A0303',
 'underlying_symbol': 'A',
 'market_tplus': 0.0,
 'symbol': '豆一0303',
 'margin_rate': 0.05,
 'maturity_date': '2003-03-14',
 'type': 'Future',
 'trading_code': 'a0303',
 'exchange': 'DCE',
 'product': 'Commodity',
 'contract_multiplier': 10.0,
 'round_lot': 1.0,
 'trading_hours': '21:01-23:00,09:01-10:15,10:31-11:30,13:31-15:00',
 'listed_date': '2002-03-15',
 'industry_name': '油脂',
 'de_listed_date': '2003-03-14',
 'underlying_order_book_id': 'null'}

In [11]:
underlying_symbols = []
vt_symbols = []   # IF99.CFFEX
for data in data_dict.values():
    # 1) Filter underlying symbol    
    underlying = data['underlying_symbol']
    if underlying not in underlying_symbols:
        underlying_symbols.append(underlying)
        
        # 2) Filter listed date
        dt_str = data["listed_date"]
        dt = datetime.strptime(dt_str, "%Y-%m-%d")
        
        if dt <= datetime(2016,1,1):
            
            vt_symbol = underlying + "99" + "." + data["exchange"]
            
            vt_symbols.append(vt_symbol)
            
    
    

In [18]:
for vt_symbol in vt_symbols:
    symbol, exchange =tuple(vt_symbol.split("."))
    download_data(symbol, Exchange(exchange))

finish! symbol= A99 count= 3661
finish! symbol= AG99 count= 2121
finish! symbol= AL99 count= 3661
finish! symbol= AU99 count= 3173
finish! symbol= B99 count= 3661
finish! symbol= BB99 count= 1739
finish! symbol= BU99 count= 1781
finish! symbol= C99 count= 3661
finish! symbol= CF99 count= 3661
finish! symbol= CS99 count= 1485
finish! symbol= CU99 count= 3661
finish! symbol= ER99 count= 994
finish! symbol= FB99 count= 1739
finish! symbol= FG99 count= 1980
finish! symbol= FU99 count= 3650
finish! symbol= HC99 count= 1670
finish! symbol= I99 count= 1774
finish! symbol= IC99 count= 1409
finish! symbol= IF99 count= 2620
finish! symbol= IH99 count= 1409
finish! symbol= J99 count= 2380
finish! symbol= JD99 count= 1759
finish! symbol= JM99 count= 1909
finish! symbol= JR99 count= 1753
finish! symbol= L99 count= 3282
finish! symbol= LR99 count= 1597
finish! symbol= M99 count= 3661
finish! symbol= MA99 count= 1612
finish! symbol= ME99 count= 860
finish! symbol= NI99 count= 1422
finish! symbol= OI9